<a href="https://colab.research.google.com/github/IamSVP94/OpenDataScience_course/blob/master/Homework/Homework%2010.%20Flight%20delays%20kaggle.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Домашнее задание № 10 (демо)<br>Прогнозирование задержек вылетов

Ваша задача – побить единственный бенчмарк в [соревновании](https://www.kaggle.com/c/flight-delays-2017) на Kaggle Inclass. Подробных инструкций не будет, будет только тезисно описано, как получен этот бенчмарк. Конечно, с помощью Xgboost. Надеюсь, на данном этапе курса вам достаточно бросить полтора взгляда на данные, чтоб понять, что это тот тип задачи, в которой затащит Xgboost. Но проверьте еще Catboost.

In [64]:
!pip install catboost

In [65]:
import numpy as np
import pandas as pd
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression

from xgboost import XGBClassifier
from catboost import CatBoostClassifier, Pool

from sklearn.metrics import roc_auc_score

In [66]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [67]:
path_to_files = '/content/drive/My Drive/Colab Notebooks/flight_delays/'
train = pd.read_csv(path_to_files+'flight_delays_train.csv')
test = pd.read_csv(path_to_files+'flight_delays_test.csv')

In [68]:
train.head()

Month DayofMonth DayOfWeek  DepTime  ... Origin Dest Distance  dep_delayed_15min
0   c-8       c-21       c-7     1934  ...    ATL  DFW      732                  N
1   c-4       c-20       c-3     1548  ...    PIT  MCO      834                  N
2   c-9        c-2       c-5     1422  ...    RDU  CLE      416                  N
3  c-11       c-25       c-6     1015  ...    DEN  MEM      872                  N
4  c-10        c-7       c-6     1828  ...    MDW  OMA      423                  Y

[5 rows x 9 columns]

In [69]:
test.head()

Month DayofMonth DayOfWeek  DepTime UniqueCarrier Origin Dest  Distance
0   c-7       c-25       c-3      615            YV    MRY  PHX       598
1   c-4       c-17       c-2      739            WN    LAS  HOU      1235
2  c-12        c-2       c-7      651            MQ    GSP  ORD       577
3   c-3       c-25       c-7     1614            WN    BWI  MHT       377
4   c-6        c-6       c-3     1505            UA    ORD  STL       258

Итак, надо по времени вылета самолета, коду авиакомпании-перевозчика, месту вылета и прилета и расстоянию между аэропортами вылета и прилета предсказать задержку вылета более 15 минут. В качестве простейшего бенчмарка возьмем логистическую регрессию и два признака, которые проще всего взять: `DepTime` и `Distance`. У такой модели результат – 0.68202 на LB. 

In [70]:
X_train, y_train = train[['Distance', 'DepTime']].values, train['dep_delayed_15min'].map({'Y': 1, 'N': 0}).values
X_test = test[['Distance', 'DepTime']].values

X_train_part, X_valid, y_train_part, y_valid = train_test_split(X_train, 
                                                                y_train, 
                                                                test_size=0.3, 
                                                                random_state=17)

In [71]:
logit = LogisticRegression(random_state=17)

logit.fit(X_train_part, y_train_part)
logit_valid_pred = logit.predict_proba(X_valid)[:, 1]

roc_auc_score(y_valid, logit_valid_pred)

0.6795697123357751

In [72]:
logit.fit(X_train, y_train)
logit_test_pred = logit.predict_proba(X_test)[:, 1]

# pd.Series(logit_test_pred, 
#           name='dep_delayed_15min').to_csv('../Data/logit_2feat.csv', 
#                                            index_label='id', 
#                                            header=True)

Как был получен бенчмарк в соревновании:
- Признаки `Distance` и  `DepTime` брались без изменений
- Создан признак "маршрут" из исходных `Origin` и `Dest`
- К признакам `Month`, `DayofMonth`, `DayOfWeek`, `UniqueCarrier` и "маршрут" применено OHE-преобразование (`LabelBinarizer`)
- Выделена отложенная выборка
- Обучалась логистическая регрессия и градиентный бустинг (xgboost), гиперпараметры бустинга настраивались на кросс-валидации, сначала те, что отвечают за сложность модели, затем число деревьев фиксировалось равным 500 и настраивался шаг градиентного спуска
- С помощью `cross_val_predict` делались прогнозы обеих моделей на кросс-валидации (именно предсказанные вероятности), настраивалась линейная смесь ответов логистической регрессии и градиентного бустинга вида $w_1 * p_{logit} + (1 - w_1) * p_{xgb}$, где $p_{logit}$ – предсказанные логистической регрессией вероятности класса 1, $p_{xgb}$ – аналогично. Вес $w_1$ подбирался вручную. 
- В качестве ответа для тестовой выборки бралась аналогичная комбинация ответов двух моделей, но уже обученных на всей обучающей выборке.

Описанный план ни к чему не обязывает – это просто то, как решение получил автор задания. Возможно, мы не захотите следовать намеченному плану, а добавите, скажем, пару хороших признаков и обучите лес из тысячи деревьев.

Удачи!

<br><hr><br>

In [73]:
from sklearn.model_selection import train_test_split

In [74]:
def df_preparation(df_train, df_test, target = 'target'):
    common = df_train.merge(df_test, how='outer', indicator=('where_is')) # объединение фреймов
    common['route'] = common['Origin'] + '-' + common['Dest']
    y = common[target].map({'Y': 1, 'N': 0})
    OHE = pd.get_dummies(common.drop([target], axis=1), prefix_sep=': ')
    
    left_indx = y[y.notna()] # индексы train
    right_indx = y[y.isna()] # индексы test

    new_df_train = OHE.loc[left_indx.index,:] # выделение df_train
    new_df_test = OHE.loc[right_indx.index,:] # выделение df_test


    return {'y_df_train': y.dropna(), 
            'df_train': new_df_train,
            'df_test': new_df_test}
 
dfs = df_preparation(train, test, target='dep_delayed_15min')

In [75]:
y_df_train = dfs['y_df_train']
df_train = dfs['df_train']
df_test = dfs['df_test']

In [76]:
X_train, X_valid, y_train, y_valid = train_test_split(df_train, 
                                                      y_df_train, 
                                                      test_size=0.3, 
                                                      random_state=2,
                                                      shuffle=True)

In [77]:
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import cross_val_predict

In [78]:
np.arange(0, 8, 1)

array([0, 1, 2, 3, 4, 5, 6, 7])

In [80]:
cat_model = CatBoostClassifier(iterations=1000, 
                               early_stopping_rounds=20, 
                               learning_rate=0.1, 
                               loss_function='Logloss', 
                               use_best_model=True, 
                               
                               verbose=True)

In [88]:
# cat_model.fit(train.drop(['dep_delayed_15min'],axis=1), train['dep_delayed_15min'])
cat_model.fit(X_train, y_train, 
              plot=True, verbose=False, 
              eval_set=(X_valid, y_valid), )

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

In [89]:
cat_model.get_all_params()

{'auto_class_weights': 'None',
 'bayesian_matrix_reg': 0.10000000149011612,
 'best_model_min_trees': 1,
 'boost_from_average': False,
 'boosting_type': 'Plain',
 'bootstrap_type': 'MVS',
 'border_count': 254,
 'class_names': [0, 1],
 'classes_count': 0,
 'depth': 6,
 'eval_metric': 'Logloss',
 'feature_border_type': 'GreedyLogSum',
 'grow_policy': 'SymmetricTree',
 'iterations': 1000,
 'l2_leaf_reg': 3,
 'leaf_estimation_backtracking': 'AnyImprovement',
 'leaf_estimation_iterations': 10,
 'leaf_estimation_method': 'Newton',
 'learning_rate': 0.10000000149011612,
 'loss_function': 'Logloss',
 'max_leaves': 64,
 'min_data_in_leaf': 1,
 'model_shrink_mode': 'Constant',
 'model_shrink_rate': 0,
 'model_size_reg': 0.5,
 'nan_mode': 'Min',
 'od_pval': 0,
 'od_type': 'Iter',
 'od_wait': 20,
 'penalties_coefficient': 1,
 'random_seed': 0,
 'random_strength': 1,
 'rsm': 1,
 'sampling_frequency': 'PerTree',
 'score_function': 'Cosine',
 'sparse_features_conflict_fraction': 0,
 'subsample': 0.800

In [119]:
y_pred = cross_val_predict(cat_model, X_valid, y_valid, cv=5)
y_pred

CatBoostError: ignored

In [ ]:
roc_auc_score(y_valid, y_pred)

### Попытка работы с кат. признаками и CatBoost

In [92]:
train

Month DayofMonth DayOfWeek  ...  Dest Distance dep_delayed_15min
0       c-8       c-21       c-7  ...   DFW      732                 N
1       c-4       c-20       c-3  ...   MCO      834                 N
2       c-9        c-2       c-5  ...   CLE      416                 N
3      c-11       c-25       c-6  ...   MEM      872                 N
4      c-10        c-7       c-6  ...   OMA      423                 Y
...     ...        ...       ...  ...   ...      ...               ...
99995   c-5        c-4       c-3  ...   RDD      199                 N
99996   c-1       c-18       c-3  ...   DAB      884                 N
99997   c-1       c-24       c-2  ...   IAH     1076                 N
99998   c-4       c-27       c-4  ...   GGG      140                 N
99999  c-11       c-17       c-4  ...   SMF      605                 N

[100000 rows x 9 columns]

In [93]:
cat_train = train.copy()
target = 'dep_delayed_15min' # целевая переменная
categorical_features_names = cat_train.drop([target], axis=1).select_dtypes('object').columns

In [94]:
cat_train[categorical_features_names].nunique()

Month             12
DayofMonth        31
DayOfWeek          7
UniqueCarrier     22
Origin           289
Dest             289
dtype: int64

In [157]:
from catboost import cv

In [175]:
cat_params = {
    'depth': np.arange(0, 8, 1), 
    
}

# l2_leaf_reg, bagging_temperature, random_strength, one_hot_max_size, max_ctr_complexity, border_count, grow_policy, early_stopping_rounds, 

In [169]:
params = {'early_stopping_rounds': 20, 
          'eval_metric': 'AUC', 
          'iterations': 10**3, 
          # 'save_snapshot': True, 
          # 'snapshot_interval':1, 
          # 'snapshot_file': path_to_files+'cat_snapshot',
          'learning_rate': 10**(-1), 
          'loss_function': 'Logloss', 
          'train_dir': path_to_files+'cat_model',}

In [167]:
cv_data = cv(params = params, 
             pool = Pool(train.drop([target], axis=1), 
                         label = train[target], 
                         cat_features = categorical_features_names), 
             fold_count = 5, 
             shuffle = True, 
             partition_random_seed = 2, 
             plot = True, 
             stratified = True, 
             verbose = 100)

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	test: 0.6757810	best: 0.6757810 (0)	total: 1.09s	remaining: 18m 13s
100:	test: 0.7494126	best: 0.7494126 (100)	total: 1m 30s	remaining: 13m 23s
200:	test: 0.7574982	best: 0.7574982 (200)	total: 3m 5s	remaining: 12m 17s
300:	test: 0.7605300	best: 0.7605300 (300)	total: 4m 40s	remaining: 10m 52s
400:	test: 0.7629260	best: 0.7629260 (400)	total: 6m 21s	remaining: 9m 29s
500:	test: 0.7641716	best: 0.7641767 (499)	total: 8m 3s	remaining: 8m 1s
600:	test: 0.7650477	best: 0.7650477 (600)	total: 9m 47s	remaining: 6m 30s
700:	test: 0.7660253	best: 0.7660253 (700)	total: 11m 34s	remaining: 4m 56s
800:	test: 0.7669272	best: 0.7669305 (799)	total: 13m 26s	remaining: 3m 20s
900:	test: 0.7677279	best: 0.7677279 (900)	total: 15m 20s	remaining: 1m 41s
Stopped by overfitting detector  (20 iterations wait)


In [95]:
df_ = cat_train.sample(frac=1, random_state=0) # перемешиваем датасет
# делим выборку на тестовую и тренировочную в соотношении 2 к 1 (66.6% и 33.3%)
df_train = df_.iloc[: 2 * len(cat_train) // 3]
df_val = df_.iloc[2 * len(cat_train) // 3 :]

In [96]:
train_pool = Pool(df_train.drop([target], axis=1), 
                  label=df_train[target], 
                  cat_features=categorical_features_names)

In [98]:
val_pool = Pool(df_val.drop([target], axis=1), 
                label=df_val[target], 
                cat_features=categorical_features_names)

In [168]:
cat_params = {
    'depth': np.arange(0, 8, 1), 
    
}

# l2_leaf_reg, bagging_temperature, random_strength, one_hot_max_size, max_ctr_complexity, border_count, grow_policy, early_stopping_rounds, 

In [154]:
cat_model = CatBoostClassifier(early_stopping_rounds=20, 
                               eval_metric='AUC', 
                               iterations = 10**3, 
                               learning_rate=0.1, 
                               loss_function='Logloss',
                               train_dir=path_to_files+'cat_model')

In [155]:
cat_model.fit(train_pool, 
              eval_set=val_pool, 
              verbose=100, 
              plot=True)

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	test: 0.6632807	best: 0.6632807 (0)	total: 167ms	remaining: 2m 46s
100:	test: 0.7494232	best: 0.7494232 (100)	total: 12.2s	remaining: 1m 48s
200:	test: 0.7577947	best: 0.7577947 (200)	total: 24.9s	remaining: 1m 38s
300:	test: 0.7609340	best: 0.7609729 (292)	total: 37.5s	remaining: 1m 27s
400:	test: 0.7620789	best: 0.7621070 (398)	total: 50.2s	remaining: 1m 15s
500:	test: 0.7628834	best: 0.7628834 (500)	total: 1m 3s	remaining: 1m 2s
Stopped by overfitting detector  (20 iterations wait)

bestTest = 0.7635128528
bestIteration = 568

Shrink model to first 569 iterations.


In [180]:
cat_model.get_feature_importance(prettified=True)

Feature Id  Importances
0        DepTime    37.829844
1  UniqueCarrier    12.546543
2         Origin    10.575894
3           Dest     9.718572
4       Distance     8.195552
5          Month     7.964120
6     DayofMonth     7.370020
7      DayOfWeek     5.799456

In [113]:
y_pred = cat_model.predict(test_pool)

In [122]:
type(y_pred)

numpy.ndarray

In [127]:
roc_auc_score([1 if i=='Y' else 0 for i in test_pool.get_label()], 
              [1 if i=='Y' else 0 for i in y_pred])

0.5773364821136084